In [1]:
import os
import pandas as pd
import numpy as np
import sys
sys.path.append('../../Scripts')
from preprocess_daily import DailyPreprocessor
from generate_signals import SignalGenerator

비보호좌회전, 신호우회전, 유턴

줄임말 목록
- `i` : 교차로번호, `inter_no`
- `f` : 진입, from, `inc_edge_id`
- `t` : 진출, to, `out_edge_id`
- `vec` : 방향벡터, unit vector (`np.array([0.6, 0.8])`)
- `dire` : 방위, direction (동, 서, 남, 북, 북동, 북서, 남동, 남서)
- `rvec` : 정방향 방향벡터, unit vector to the right direction (`np.array([0,1])`)

필요한 객체들 목록

- `inter2dire2rvec` : `inter_no` $\mapsto$ `dire2rvec`
  - `dire2rvec` : `dire` $\mapsto$ `rvec`
- `inter2incs` : `inter_no` $\mapsto$ `inc_edge_ids`
- `inter2outs` : `inter_no` $\mapsto$ `out_edge_ids`
- `inter2inc2dire` : `inter_no` $\mapsto$ `int2dire`
  - `inc2dire` : `out_edge_id` $\mapsto$ `dire`
- `inter2out2dire` : `inter_no` $\mapsto$ `out2dire`
  - `out2dire` : `inc_edge_id` $\mapsto$ `dire`
- `inter2inc2vec` : `inter_no` $\mapsto$ `int2vec`
  - `inc2vec` : `out_edge_id` $\mapsto$ `vec`
- `inter2out2vec` : `inter_no` $\mapsto$ `out2vec`
  - `out2vec` : `inc_edge_id` $\mapsto$ `vec`

좌회전 판단

Given `inter_no`, `inc_edge_id` and `out_edge_id`, we have `inc_vec = inter2inc2vec[inter_no][inc_edge_id]` and `out_vec = inter2out2vec[inter_no][out_edge_id]`.
Rotate `inc_vec` by 90, 180 and 270 degrees clockwise, to define 
`out_vec_left`, `out_vec_straight` and `out_vec_right`.
Define `out_vecs={'right':out_vec_left, 'straight':out_vec_straight, 'right':out_vec_right}`.
Select the key that maximize the similarity of the corresponding value of the key and `inc_vec`.

In [2]:
self = DailyPreprocessor()
self.main()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.
2. 중간산출물을 생성합니다.
2-1. 매칭 테이블들을 생성했습니다.
2-2. 비보호우회전(g)을 배정했습니다.
2-3. 직진 및 좌회전(G)을 배정했습니다.
2-2. node2num_cycles.json를 저장했습니다.
3. 이슈사항을 저장합니다.


In [19]:
for i, row in self.match5.iterrows():
    node_id = row.node_id
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    if not (pd.isna(inc_edge_id) and pd.isna(out_edge_id)):
        turn_type = n2io2turn[node_id][(inc_edge_id, out_edge_id)]
        self.match5.at[i, 'turn_type']=turn_type
display(self.match5)

inter_no  phase_no ring_type  move_no inc_dire out_dire inc_angle  \
0        175         1         A        8        남        북       179   
1        175         1         B        4        북        남       001   
2        175         2         A        7        북        동       001   
3        175         2         B        3        남        서       179   
4        175         3         A        6        동        서       090   
5        175         3         B        1        동        남       090   
6        175         4         A        5        서        북       270   
7        175         4         B        2        서        동       270   
8        176         1         A        8        남        북       180   
9        176         1         B        4        북        남       359   
10       176         2         A        8        남        북       180   
11       176         2         B        3        남        서       180   
12       176         3         A        5        서        북       270   
13       176         3         B       18      NaN      NaN       NaN   
14       177         1         A        8        남        북       179   
15       177         1         B        4        북        남       000   
16       177         2         A        7        북        동       000   
17       177         2         B        3        남        서       179   
18       177         3         A       17      NaN      NaN       NaN   
19       177         3         B       18      NaN      NaN       NaN   
20       177         4         A        5        서        북       268   
21       177         4         B        1        동        남       090   
22       178         1         A        8        남        북       180   
23       178         1         B        4        북        남       000   
24       178         2         A        7        북        동       000   
25       178         2         B        3        남        서       180   
26       178         3         A        5        서        북       270   
27       178         3         B        2        서        동       270   
28       178         4         A        6        동        서       090   
29       178         4         B        1        동        남       090   
30       201         1         A        8        남        북       180   
31       201         1         B        3        남        서       180   
32       201         2         A        5        서        북       270   
33       201         2         B        2        서        동       270   
34       201         3         A        6        동        서       090   
35       201         3         B        2        서        동       270   
36       201         4         A        6        동        서       090   
37       201         4         B        1        동        남       090   
38       201         5         A        7        북        동       000   
39       201         5         B        4        북        남       000   
40       202         1         A        6        동        서       090   
41       202         1         B        2        서        동       270   
42       202         2         A       17      NaN      NaN       NaN   
43       202         2         B       18      NaN      NaN       NaN   
44       206         1         A        8        남        북       180   
45       206         1         B        4        북        남       000   
46       206         2         A       17      NaN      NaN       NaN   
47       206         2         B       18      NaN      NaN       NaN   
48       206         3         A        8        남        북       180   
49       206         3         B        4        북        남       000   
50       206         4         A       17      NaN      NaN       NaN   
51       206         4         B       18      NaN      NaN       NaN   
52       210         1         A        6        동        서       090   
53       210         1         B       18      NaN      NaN   

In [15]:
for row in self.match5.itertuples():
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id
    inc_edge = self.net.getEdge(inc_edge_id)
    out_edge = self.net.getEdge(out_edge_id)
    print(len(inc_edge.getConnections(out_edge)))

4
2
1
1
2
1
1
1
3
2
3
1
2


KeyError: nan

In [4]:
self.load_data()
self.make_match1()
self.make_match2()
self.make_match3()
self.make_match4()
self.make_match5()

1. 데이터를 로드합니다.
1-1. 네트워크가 로드되었습니다.
1-2. 테이블들이 로드되었습니다.
1-3. 네트워크의 모든 clean state requirement들을 체크했습니다.
1-4. 테이블들의 무결성 검사를 완료했습니다.
1-5. 주요 객체 (리스트, 딕셔너리)들을 저장했습니다.


In [5]:
display(self.uturn)
display(self.u_turn)
display(self.u_condition)

self.u_turn = pd.merge(self.u_turn, self.u_condition, on='child_id')
self.u_turn

parent_id child_id direction condition      inc_edge_id      out_edge_id
0        i0      u00         북      좌회전시     571500487_02  571500487_01.32
1        i2      u20         북     보행신호시  571542810_01.51     571542810_02
2        i3      u30         북     보행신호시     571556452_01     571556452_02
3        i3      u31         동     보행신호시     571500475_02  571500475_01.26
4        i3      u32         서     보행신호시     571540303_02    -571540303_02
5        i6      u60         서      좌회전시     571500535_02    -571500535_02

parent_id child_id     head_edge_id      inc_edge_id      out_edge_id
0        i0      u00    -571500487_01     571500487_02  571500487_01.32
1        i2      u20     571542811_02  571542810_01.51     571542810_02
2        i3      u30     571556450_02     571556452_01     571556452_02
3        i3      u31    -571500475_01     571500475_02  571500475_01.26
4        i3      u32  571540303_02.21     571540303_02    -571540303_02
5        i6      u60  571500535_02.18     571500535_02    -571500535_02

child_id condition
0      u00      좌회전시
1      u20     보행신호시
2      u30     보행신호시
3      u31     보행신호시
4      u32     보행신호시
5      u60      좌회전시

parent_id child_id     head_edge_id      inc_edge_id      out_edge_id  \
0        i0      u00    -571500487_01     571500487_02  571500487_01.32   
1        i2      u20     571542811_02  571542810_01.51     571542810_02   
2        i3      u30     571556450_02     571556452_01     571556452_02   
3        i3      u31    -571500475_01     571500475_02  571500475_01.26   
4        i3      u32  571540303_02.21     571540303_02    -571540303_02   
5        i6      u60  571500535_02.18     571500535_02    -571500535_02   

  condition  
0      좌회전시  
1     보행신호시  
2     보행신호시  
3     보행신호시  
4     보행신호시  
5      좌회전시

In [10]:
cmatches = []
i = 0
row = self.u_turn.iloc[0]
print(row)
child_id = row.child_id
parent_id = row.parent_id
condition = row.condition
inc_edge_id = row.inc_edge_id
out_edge_id = row.out_edge_id
cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
cmatch['node_id'] = child_id

parent_id                    i0
child_id                    u00
head_edge_id      -571500487_01
inc_edge_id        571500487_02
out_edge_id     571500487_01.32
condition                  좌회전시
Name: 0, dtype: object


In [ ]:
# 각 uturn node에 대하여 (inc_edge_id, out_edge_id) 부여
cmatches = []
for _, row in self.uturn.iterrows():
    child_id = row.child_id
    parent_id = row.parent_id
    dire = row.direction
    condition = row.condition
    inc_edge_id = row.inc_edge_id
    out_edge_id = row.out_edge_id

    print(parent_id, condition)

    # match5에서 부모노드id에 해당하는 행들을 가져옴 (cmatch)
    cmatch = self.match5.copy()[self.match5.node_id==parent_id] # match dataframe for a child node
    cmatch = cmatch.sort_values(by=['phase_no', 'ring_type']).reset_index(drop=True)
    cmatch['node_id'] = child_id
    cmatch[['inc_edge_id', 'out_edge_id']] = np.nan
    display(cmatch)

    # 보행신호시/좌회전시 진입/진출방향
    ind = self.dires.index(dire)
    inc_dire_pedes = self.dires[(ind + 2) % len(self.dires)]
    out_dire_pedes = self.dires[(ind - 2) % len(self.dires)]
    inc_dire_right = dire
    out_dire_right = self.dires[(ind + 2) % len(self.dires)]

    if condition == '보행신호시':
        print(inc_dire_pedes, out_dire_pedes)
    else:
        print(inc_dire_right, out_dire_right)

    # 보행신호시/좌회전시 조건
    pedes_exists = (cmatch.inc_dire==inc_dire_pedes) & (cmatch.out_dire==out_dire_pedes)
    right_exists = (cmatch.inc_dire==inc_dire_right) & (cmatch.out_dire==out_dire_right)

    # 보행신호시/좌회전시 진입/진출 엣지id 배정
    ind = self.dires.index(dire)
    if condition == "보행신호시":
        cmatch.loc[pedes_exists, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
    elif condition == "좌회전시":
        cmatch.loc[right_exists, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
    display(cmatch)

    # 신호없음이동류발생시/보행신호이동류발생시 조건
    all_redsigns = cmatch.move_no == 18
    crosswalk_on = cmatch.move_no == 17

    # 만약 어떤 유턴신호도 배정되지 않았다면
    # 좌회전시 → 보행신호시 → 보행신호이동류발생시 → 신호없음이동류발생시 순으로 진입/진출 엣지id 배정
    uturn_not_assigned = cmatch[['inc_edge_id','out_edge_id']].isna().any(axis=1).all()
    if uturn_not_assigned:
        # 좌회전시
        if right_exists.any():
            cmatch.loc[right_exists, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 보행신호시
        elif pedes_exists.any():
            cmatch.loc[pedes_exists, ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 보행신호이동류(17) 발생시
        elif crosswalk_on.any():
            cmatch.loc[crosswalk_on & (cmatch.out_dire!=dire), ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
        # 신호없음이동류(18) 발생시
        elif all_redsigns.any():
            cmatch.loc[all_redsigns & (cmatch.out_dire!=dire), ['inc_edge_id', 'out_edge_id']] = [inc_edge_id, out_edge_id]
    display(cmatch)
cmatches.append(cmatch)


In [51]:
nodes = self.net.getNodes()
for node in nodes:
    node_id = node.getID()
    print(node_id)
    conns = [con for con in node.getConnections()]
    for con in conns:
        print(con.getJunctionIndex(), con.getTLLinkIndex(), con.getDirection())
    print()

u31
5 5 s
6 6 s
7 7 s
0 0 s
1 1 s
2 2 s
3 3 s
4 4 t

i3
5 5 r
6 6 s
7 7 s
8 8 s
9 9 l
15 15 r
16 16 s
17 17 s
18 18 s
19 19 l
10 10 r
11 11 s
12 12 s
13 13 s
14 14 l
0 0 r
1 1 s
2 2 s
3 3 s
4 4 l

u00
5 5 s
6 6 s
7 7 s
8 8 s
0 0 s
1 1 s
2 2 s
3 3 s
4 4 t

i0
0 0 r
1 1 s
2 2 s
3 3 l
8 8 r
9 9 s
10 10 s
11 11 s
12 12 s
13 13 l
14 14 r
15 15 s
16 16 l
4 4 r
5 5 s
6 6 s
7 7 l

u60
0 0 s
1 1 s
2 2 s
3 3 s
4 4 s
5 5 s
6 6 s
7 7 s
8 8 t

d12

n13
0 -1 s
1 -1 s
2 -1 s
3 -1 s
4 -1 s

i8
8 8 r
9 9 s
10 10 s
11 11 l
0 0 r
1 1 s
2 2 s
3 3 l
4 4 s
5 5 s
6 6 s
7 7 l
12 12 r
13 13 s
14 14 s
15 15 l

i9
2 2 s
3 3 s
0 0 s
1 1 s

n14
2 -1 r
3 -1 s
4 -1 s
5 -1 s
6 -1 s
7 -1 l
0 -1 r
1 -1 l

n11
3 -1 s
4 -1 s
0 -1 s
1 -1 s
2 -1 s

i7
4 4 r
5 5 s
6 6 s
3 3 r
0 0 s
1 1 s
2 2 l

u32
0 0 s
1 1 s
2 2 s
3 3 s
4 4 s
5 5 s
6 6 s
7 7 t

n06
0 -1 s
1 -1 s
2 -1 s
3 -1 s
4 -1 s
5 -1 s
6 -1 s

n09
4 -1 s
5 -1 s
6 -1 s
0 -1 s
1 -1 s
2 -1 s
3 -1 s

i6
4 4 r
5 5 s
6 6 s
7 7 s
8 8 l
12 12 r
13 13 s
14 14 s
15 15 l
9 9 r
1

In [ ]:
'''Given `inter_no`, `inc_edge_id` and `out_edge_id`, we have `inc_vec = inter2inc2vec[inter_no][inc_edge_id]` and `out_vec = inter2out2vec[inter_no][out_edge_id]`.
Rotate `inc_vec` by 90, 180 and 270 degrees clockwise, to define 
`out_vec_left`, `out_vec_straight` and `out_vec_right`.
Define `out_vecs={'right':out_vec_left, 'straight':out_vec_straight, 'right':out_vec_right}`.
Select the key that maximize the similarity of the corresponding value of the key and `inc_vec`.'''